In [ ]:
import sys
import os
sys.path.append(os.path.join(os.getcwd(), '..', 'src'))

# feature engineering
the next step is to prepare the data set for machine learning. this includes
- selecting useful columns
- handling missing values
- cleaning up unrealistic values in input 
- transforming values into form/format appropriate for machine learning.
- 
by intuition, we can expect the following fields to be influential when it comes to the propensity to buy.
- salary (seen in the exploratory data analysis to have an impact)
- demographics:
    + age
    + rough location
- when visited:
    + year        (trend)
    + month       (seasonality) 
    + day of week (seasonality)
    + time of day (seasonality
- engagement on site
    + time spent
    + number of options viewed
    + last step reached
    + cost of last vehicle considered

In [43]:
import duckdb
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from   utils import map_postcodes_to_area_code

In [54]:
with duckdb.connect(database='../data/propensity_to_buy.duckdb', read_only=True) as con:
    sales_df = con.sql("SELECT * FROM sales;").df()
display(sales_df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 14 columns):
 #   Column                     Non-Null Count  Dtype         
---  ------                     --------------  -----         
 0   lead_id                    50000 non-null  int64         
 1   lead_entry_time            50000 non-null  datetime64[us]
 2   has_placed_order           50000 non-null  bool          
 3   time_order_placed          6500 non-null   datetime64[us]
 4   salary                     49750 non-null  float64       
 5   date_of_birth              50000 non-null  datetime64[us]
 6   postcode                   49750 non-null  object        
 7   n_engaged_minutes          49750 non-null  float64       
 8   n_of_cars_viewed           50000 non-null  int64         
 9   company_industry           49750 non-null  object        
 10  day_of_week                50000 non-null  int64         
 11  price_of_last_car_viewed   50000 non-null  float64       
 12  step

None

# group high cardinality categorical variables. 
post codes and company industries can be grouped together.
post codes and company industries have far too high a cardinality to be useful for modelling as they stand. since all categories have roughtly equal counts of leads, not possibl to just just largest and lump the rest into 'others'. instead try to collect them into super-categories.

In [55]:
industry_mapping = {
    # product-and-engineering, techy buzzwords
    'Tech'                                    :'product-and-engineering',
    'revolutionize granular users'            :'product-and-engineering',
    'optimize world-class interfaces'         :'product-and-engineering',
    'deploy leading-edge niches'              :'product-and-engineering',
    'reinvent bricks-and-clicks partnerships' :'product-and-engineering',
    'implement dot-com content'               :'product-and-engineering',
    'optimize turn-key communities'           :'product-and-engineering',
    'benchmark cutting-edge e-services'       :'product-and-engineering',
    'e-enable revolutionary web services'     :'product-and-engineering',
    'transition enterprise paradigms'         :'product-and-engineering',
    'empower distributed e-services'          :'product-and-engineering',
    'utilize dot-com paradigms'               :'product-and-engineering',
    'brand visionary relationships'           :'product-and-engineering',
    'utilize cross-media paradigms'           :'product-and-engineering',
    'e-enable interactive eyeballs'           :'product-and-engineering',
    'scale intuitive e-commerce'              :'product-and-engineering',
    'deliver collaborative portals'           :'product-and-engineering',
    'synthesize customized models'            :'product-and-engineering',
    'repurpose user-centric functionalities'  :'product-and-engineering',
    'embrace rich models'                     :'product-and-engineering', # ... or fashion? :)
    'utilize out-of-the-box models'           :'product-and-engineering',
    'grow back-end synergies'                 :'product-and-engineering',
    'cultivate global infrastructures'        :'product-and-engineering',
    'innovate cutting-edge functionalities'   :'product-and-engineering',
    'unleash plug-and-play infrastructures'   :'product-and-engineering',
    're-intermediate intuitive niches'        :'product-and-engineering',
    'leverage integrated action-items'        :'product-and-engineering',
    'matrix bricks-and-clicks e-tailers'      :'product-and-engineering',
    'facilitate efficient infrastructures'    :'product-and-engineering',
    'reinvent ubiquitous users'               :'product-and-engineering',
    'iterate efficient platforms'             :'product-and-engineering',
    'implement next-generation e-services'    :'product-and-engineering',
    'implement frictionless eyeballs'         :'product-and-engineering',
    'streamline value-added experiences'      :'product-and-engineering',
    'integrate enterprise technologies'       :'product-and-engineering',
    'scale scalable solutions'                :'product-and-engineering',
    'orchestrate value-added eyeballs'        :'product-and-engineering',
    'visualize best-of-breed networks'        :'product-and-engineering',
    
    # manufacturing
    'Manufacturing':'manufacturing-automotive',
    'Automotive'   :'manufactoring-automotive',
    
    # financial Services
    'Finance'     : 'financial-services',
    'Real Estate' : 'financial-services',
    
    # retail
    'Retail'                             :'retail',
    'generate virtual e-commerce'        :'retail',
    'monetize value-added supply-chains' :'retail',
    'optimize impactful e-tailers'       :'retail',
    'incubate dynamic e-tailers'         :'retail',

    # government and public services
    'Government' : 'public-sector',
    'Education'  : 'public-sector',
    'Healthcare' : 'public-sector',
    
    # incomprehensible buzzwords
    'Consulting'                        :'consulting-professional-services',
    'cultivate enterprise deliverables' :'consulting-professional-services',
    'engineer proactive relationships'  :'consulting-professional-services',
    'generate global e-business'        :'consulting-professional-services',
    'transition sticky communities'     :'consulting-professional-services',
    'facilitate proactive bandwidth'    :'consulting-professional-services',
    'facilitate end-to-end paradigms'   :'consulting-professional-services',
    'mesh robust partnerships'          :'consulting-professional-services',
    'leverage strategic action-items'   :'consulting-professional-services',
    'transform extensible paradigms'    :'consulting-professional-services',

    # blanks:
    '': 'unknown'
}


In [74]:
feature_engineered = (
    sales_df
    # categorise non-quantitative variables:
    .assign(how_did_you_hear_about_us = sales_df['how_did_you_hear_about_us'].astype('category'))
    .assign(company_industry          = sales_df['company_industry'].fillna('unknown').astype('category'))
    .assign(step_reached_in_website   = sales_df['step_reached_in_website'].astype('category'))
    .assign(day_of_week               = sales_df['day_of_week'].astype('category'))
    # transform timestamp to categorical
    .assign(entry_month               = sales_df['lead_entry_time'].dt.month.astype('category'))  # seasonality?
    .assign(entry_hour                = sales_df['lead_entry_time'].dt.hour.astype('category'))  # seasonality?
    # engineer new features out of timestamps
    .assign(age_at_entry              = (sales_df['lead_entry_time']-sales_df['date_of_birth']).dt.days/365.25)
    # engineer area code from postcode (grab anything before the first digit, retain only most popular)
    .assign(area_code                 = sales_df['postcode'].fillna('other').apply(map_postcodes_to_area_code)) 
    # quantitative fields: assume missing salaries and negative salaries are 0.00
    .assign(salary                    = sales_df['salary'].fillna(0.00).clip(lower=0.00)) 
    # trend?
    .assign(entry_year                = sales_df['lead_entry_time'].dt.year.astype('int'))
    # curtail unrealistic session lengths
    .assign(n_engaged_minutes         = sales_df['n_engaged_minutes'].fillna(0).clip(upper=140))
    .assign(minutes_per_car           = np.where(sales_df['n_of_cars_viewed']>0,sales_df['n_engaged_minutes']/sales_df['n_of_cars_viewed'],0))
    .assign(minutes_per_car           = lambda df_: df_['minutes_per_car'].fillna(0).clip(upper=60))
    # assume price is monthly leasing fee, is it within 20% of income?
    .assign(affordability_ratio       = np.where(sales_df['salary']>0, (sales_df['price_of_last_car_viewed']*12)/(sales_df['salary']*0.2), 10))
    .assign(affordability_ratio       = lambda df_:df_['affordability_ratio'].clip(upper=10))
    .assign(industry_categories       = sales_df['company_industry'].map(industry_mapping).fillna('unknown'))
    # drop columns not used for machine learning
    .drop(columns=[
        'lead_entry_time',     # replaced by entry_year, entry_month
        'time_order_placed',   # only known at time of ordering
        'date_of_birth',       # replaced by age_at_entry
        'postcode',            # replaced by area_code
        'company_industry',    # replaced by industry_categories
    ])
    # set lead_id as index
    .set_index('lead_id')
)

feature_engineered.sample(10)

has_placed_order     salary  n_engaged_minutes  n_of_cars_viewed  \
lead_id                                                                     
15505               False   64110.03               6.94                11   
54930               False   54468.93              11.03                13   
41185               False   62828.76              27.77                 0   
34186               False   59758.09               5.23                 7   
33045               False   63659.11               3.97                 0   
43235               False   46778.00              20.12                10   
32253               False   87144.60               3.68                 3   
48241               False   45466.44              23.22                 2   
59344                True  110682.50               2.82                 0   
57214               False  103120.11              24.61                 3   

        day_of_week  price_of_last_car_viewed step_reached_in_website  \
lead_id                                                                 
15505             2                    482.08          car_configured   
54930             1                    394.13             car_clicked   
41185             2                    508.66                homepage   
34186             2                    472.61          car_configured   
33045             3                    399.74                homepage   
43235             1                    453.06         quote_generated   
32253             3                    418.85         quote_generated   
48241             6                    452.97         quote_generated   
59344             4                    467.13                homepage   
57214             0                    412.55         quote_generated   

        how_did_you_hear_about_us entry_month entry_hour  age_at_entry  \
lead_id                                                                  
15505                       other           6         14     67.025325   
54930        company benefit page           8         17     22.603696   
41185        company benefit page          10          0     46.704997   
34186                       other           8          7     33.546886   
33045                      google           7         13     29.982204   
43235               word of mouth           6         21     54.469541   
32253                    linkedin           3         20     30.814511   
48241                       other          12         14     21.571526   
59344                      google           6         12     35.529090   
57214                       other           7         10     28.188912   

        area_code  entry_year  minutes_per_car  affordability_ratio  \
lead_id                                                               
15505       other        2025         0.630909             0.451174   
54930           W        2024         0.848462             0.434152   
41185           G        2024         0.000000             0.485758   
34186       other        2024         0.747143             0.474523   
33045       other        2025         0.000000             0.376763   
43235           S        2025         2.012000             0.581119   
32253       other        2025         1.226667             0.288383   
48241           E        2024        11.610000             0.597764   
59344           G        2025         0.000000             0.253227   
57214       other        2025         8.203333             0.240040   

                      industry_categories  
lead_id                                    
15505             product-and-engineering  
54930                              retail  
41185             product-and-engineering  
34186    consulting-professional-services  
33045    consulting-professional-services  
43235             product-and-engineering  
32253             product-and-engineering  
48241             product-and-engineering  
59344             product

In [75]:
feature_engineered.info()

<class 'pandas.core.frame.DataFrame'>
Index: 50000 entries, 10000 to 59999
Data columns (total 16 columns):
 #   Column                     Non-Null Count  Dtype   
---  ------                     --------------  -----   
 0   has_placed_order           50000 non-null  bool    
 1   salary                     50000 non-null  float64 
 2   n_engaged_minutes          50000 non-null  float64 
 3   n_of_cars_viewed           50000 non-null  int64   
 4   day_of_week                50000 non-null  category
 5   price_of_last_car_viewed   50000 non-null  float64 
 6   step_reached_in_website    50000 non-null  category
 7   how_did_you_hear_about_us  50000 non-null  category
 8   entry_month                50000 non-null  category
 9   entry_hour                 50000 non-null  category
 10  age_at_entry               50000 non-null  float64 
 11  area_code                  50000 non-null  object  
 12  entry_year                 50000 non-null  int64   
 13  minutes_per_car            50000

In [76]:
feature_engineered.describe()

salary  n_engaged_minutes  n_of_cars_viewed  \
count   50000.000000       50000.000000      50000.000000   
mean    56416.876915          19.772220          4.518260   
std     22401.408396          14.147616          4.831395   
min         0.000000           0.000000          0.000000   
25%     41543.287500           9.420000          0.000000   
50%     55860.800000          16.590000          3.000000   
75%     70941.950000          26.650000          9.000000   
max    598374.160000         140.000000         14.000000   

       price_of_last_car_viewed  age_at_entry   entry_year  minutes_per_car  \
count              50000.000000  50000.000000  50000.00000     50000.000000   
mean                 450.299871     46.954581   2024.56108         2.727363   
std                   49.956064     15.234699      0.49626         5.531538   
min                  239.310000     20.010951   2024.00000         0.000000   
25%                  416.480000     33.819302   2024.00000         0.000000   
50%                  450.220000     46.906229   2025.00000         0.907143   
75%                  484.100000     60.112252   2025.00000         2.967500   
max                  647.660000     73.943874   2025.00000        60.000000   

       affordability_ratio  
count         50000.000000  
mean              0.681151  
std               1.032319  
min               0.044924  
25%               0.375728  
50%               0.483640  
75%               0.655651  
max              10.000000

In [77]:
with duckdb.connect(database='../data/propensity_to_buy.duckdb', read_only=False) as con:
    con.sql("DROP TABLE IF EXISTS feature_engineered; CREATE TABLE feature_engineered AS SELECT * FROM feature_engineered")
    print(con.sql("SELECT COUNT(*) FROM feature_engineered;"))


┌──────────────┐
│ count_star() │
│    int64     │
├──────────────┤
│        50000 │
└──────────────┘



In [70]:
import datetime
print('last updated at:', datetime.datetime.now().strftime('%Y-%m-%d %H:%M'))

last updated at: 2025-08-26 02:38


In [71]:
from ydata_profiling import ProfileReport
profile = ProfileReport(feature_engineered, title="profiling report -- oskar holm")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 16/16 [00:00<00:00, 816.79it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [78]:
profile.to_file("../notes/feature_engineered_eda_report.html")

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]